# **2022218028 서영진**

# **서울시 공공 와이파이 위치 데이터 기반 서비스 분석 및 시각화**

# **목표**
자치구 단위: 생활인구 1만 명당 와이파이 설치 수 산출 → 자치구 간 형평성 평가

공간 단위: 실제 커버 반경을 고려하여 **사각지대(미커버 지역)**를 탐지 → 빨간 원으로 시각화

이를 통해 데이터 기반의 설치 의사결정을 지원



# **목적**

서울시의 **생활인구(유동인구)**와 공공 와이파이 설치 위치를 종합 분석해

생활인구 수 대비 공공와이파이 설치 수를 비교하고 와이파이가 부족한 자치구를 파악하여

실제 커버리지 미달 지역을 공간적으로 탐색하고

추가 설치가 필요한 위치를 제안함.


# **배경**
서울특별시는 시민 편의를 위해 각 자치구에 공용 와이파이를 설치해 왔지만,
설치 기준이 일관되지 않아 인구 밀집 지역에 비해 부족한 지역이 존재할 수 있다.
본 분석은

[서울시 공공와이파이 서비스 위치 정보](https://data.seoul.go.kr/dataList/OA-20883/S/1/datasetView.do) 및 [서울특별시 실시간 인구API](https://data.seoul.go.kr/dataList/OA-21778/A/1/datasetView.do)를 활용하여, 와이파이 설치의 불균형을 개선하고자 한다.

# **상세 설명**
사용 데이터
서울시 공공와이파이 서비스 위치 정보.csv
이 데이터는 서울시 각 자치구의 공공 와이파이 위치 정보, 위경도 좌표, 주소 등을 포함합니다.

**사용된 주요 라이브러리**
pandas: 데이터 전처리

folium: 지도 시각화

sklearn: 클러스터링 분석

geopy: 거리 계산

scipy.spatial.ConvexHull: 클러스터 영역 표시

**과정 및 접근 방식**
데이터 업로드 및 전처리

좌표 유효성 검증 및 자치구별 필터링

지도 시각화 (Folium 활용)

KMeans 기반 클러스터링 및 중심점 시각화

Convex Hull로 영역 외곽 경계 시각화

커버리지 부족 지역(빨간 원) 자동 탐지 시도

**선택 방법의 근거**
KMeans: 거리 기반 클러스터링에 적합하며, 지도 위 클러스터 중심점 파악에 효율적

ConvexHull: 클러스터의 대략적 경계선을 표현할 수 있어 시각적으로 유용

Folium: 위치 기반 시각화를 인터랙티브하게 제공

# **필요한 라이브러리 불러오기**

# **서울시 공공와이파이 서비스 위치 정보.csv 업로드하기**

In [ ]:
!pip install folium scikit-learn
!pip install geopandas folium
!pip install geopandas shapely pyproj folium

import geopandas as gpd
import pandas as pd
import folium
from folium.plugins import MarkerCluster, HeatMap
from sklearn.cluster import KMeans
from geopy.distance import geodesic
from scipy.spatial import ConvexHull
from google.colab import files
import random
import requests
from shapely.geometry import Point, shape
from shapely.ops import transform, unary_union
from pyproj import Transformer
import json
import numpy as np

uploaded = files.upload()
wifi_df = pd.read_csv("서울시 공공와이파이 서비스 위치 정보.csv", encoding='cp949')  # https://data.seoul.go.kr/dataList/OA-20883/S/1/datasetView.do

Saving 서울시 공공와이파이 서비스 위치 정보.csv to 서울시 공공와이파이 서비스 위치 정보.csv


# **서울시 공공와이파이 서비스 위치 정보.csv 데이터를 불러오기**

In [ ]:
wifi_df.head()

관리번호  자치구            와이파이명           도로명주소             상세주소 설치위치(층)  \
0  24서울-0002   중구     서울시청 서소문제1청사         덕수궁길 15  1동 13층 정동전망대 카페  1동 13층   
1  24서울-0003  성동구  성동구청 송정동 공공복합청사        송정18가길 9      5층 TPS 옆 천장     NaN   
2  24서울-0004  성동구  성동구청 송정동 공공복합청사        송정18가길 9     5층 도서실 입구 천장     NaN   
3  24서울-0005  강동구           강동리본센터  강동구 양재대로81길 73         3층 정수기 위     NaN   
4  24서울-0006  강동구           강동리본센터  강동구 양재대로81길 73   3층 이론교육장 복도 천장     NaN   

                    설치유형          설치기관   서비스구분  망종류  설치년도 실내외구분 wifi접속환경  \
0                4. 문화관광  디지털뉴딜(LG U+)  공공WiFi  임대망  2024    실내      NaN   
1  7-2-2. 공공 - 구의회 및 보건소  디지털뉴딜(LG U+)  공공WiFi  임대망  2024    실내      NaN   
2  7-2-2. 공공 - 구의회 및 보건소  디지털뉴딜(LG U+)  공공WiFi  임대망  2024    실내      NaN   
3           6-6. 복지 - 기타  디지털뉴딜(LG U+)  공공WiFi  임대망  2024    실내      NaN   
4           6-6. 복지 - 기타  디지털뉴딜(LG U+)  공공WiFi  임대망  2024    실내      NaN   

         Y좌표        X좌표                   작업일자  
0  37.564327  126.97565  2025-06-11 11:17:42.0  
1  37.554222  127.06895  2025-06-11 11:17:42.0  
2  37.554222  127.06895  2025-06-11 11:17:42.0  
3  37.523857  127.13023  2025-06-11 11:17:42.0  
4  37.523857  127.13023  2025-06-11 11:17:42.0

# **서울시 공공와이파이 서비스 위치 정보.csv 데이터를 HeatMap(히트맵) 방식으로 시각화**

In [ ]:
# 1. CSV 불러오기 (파일 경로에 맞게 수정)
df = pd.read_csv("서울시 공공와이파이 서비스 위치 정보.csv", encoding='cp949')

# 2. 좌표 결측값 제거 및 유효 범위 필터링
wifi_df = df[
    (df['X좌표'].between(126.76, 127.20)) &
    (df['Y좌표'].between(37.40, 37.70))
].dropna(subset=['X좌표', 'Y좌표'])

# 3. 지도 생성 (서울 중심 기준)
seoul_map = folium.Map(location=[37.5665, 126.9780], zoom_start=11)

# 4. HeatMap 데이터 생성
heat_data = list(zip(wifi_df['Y좌표'], wifi_df['X좌표']))

# 5. HeatMap 레이어 추가
HeatMap(heat_data, radius=10, blur=15, max_zoom=13).add_to(seoul_map)

# 6. 결과 출력 (Jupyter Notebook에서 자동으로 보여짐)
seoul_map


# **자치구별 생활인구 데이터 불러오기**



In [ ]:
# 인증키
api_key = "" #서울시 실시간 도시데이터 API키

# API 요청
url = f"http://openapi.seoul.go.kr:8088/{api_key}/json/SPOP_DAILYSUM_JACHI/1/1000/20240601"
response = requests.get(url)
data = response.json()

# 데이터프레임 변환
population_df = pd.DataFrame(data['SPOP_DAILYSUM_JACHI']['row'])
population_df.head()

STDR_DE_ID SIGNGU_CODE_SE SIGNGU_NM    TOT_LVPOP_CO        LVPOP_CO  \
0   20240601          11000       서울시  10628652.79170  10072633.19930   
1   20240601          11110       종로구    300667.72410    267344.74160   
2   20240601          11140        중구    286541.01980    228777.62000   
3   20240601          11170       용산구    302802.46480    276218.41400   
4   20240601          11200       성동구    345720.66090    327663.20170   

  LNGTR_STAY_FRGNR_CO SRTPD_STAY_FRGNR_CO DAIL_MXMM_LVPOP_CO  \
0        382999.89050        173019.70180     10812214.99060   
1         17377.64630         15945.33620       410405.75520   
2         18197.36050         39566.03930       410490.04890   
3         15952.23400         10631.81680       340484.67110   
4         14704.48080          3352.97830       366232.34100   

  DAIL_MUMM_LVPOP_CO    DAY_LVPOP_CO  NIGHT_LVPOP_CO DAIL_MXMM_MVMN_LVPOP_CO  \
0     10452709.61130  10734433.13470  10553095.40370           4920267.31550   
1       227716.62270    366230.01830    253837.51390            233481.90520   
2       207798.36270    358943.08580    234825.25830            244418.92690   
3       271396.83280    322574.97390    288679.24410            174487.40130   
4       334199.41080    354191.32930    339670.18340            175256.10450   

  SU_ELSE_INFLOW_LVPOP_CO SAM_ADSTRD_MVMN_LVPOP_CO SIGNGU_MVMN_LVPOP_CO  
0           1332940.25240            1806402.55970        1780924.50340  
1             83986.68740              25313.98120         124181.23660  
2             91773.92760              23853.05710         128791.94220  
3             58775.35660              38299.21110          77412.83360  
4             42909.70440              51476.88510          80869.51500

**컬럼명 확인용**

In [ ]:
population_df.columns

Index(['STDR_DE_ID', 'SIGNGU_CODE_SE', 'SIGNGU_NM', 'TOT_LVPOP_CO', 'LVPOP_CO',
       'LNGTR_STAY_FRGNR_CO', 'SRTPD_STAY_FRGNR_CO', 'DAIL_MXMM_LVPOP_CO',
       'DAIL_MUMM_LVPOP_CO', 'DAY_LVPOP_CO', 'NIGHT_LVPOP_CO',
       'DAIL_MXMM_MVMN_LVPOP_CO', 'SU_ELSE_INFLOW_LVPOP_CO',
       'SAM_ADSTRD_MVMN_LVPOP_CO', 'SIGNGU_MVMN_LVPOP_CO'],
      dtype='object')

# **자치구별 생활인구 데이터를 HeatMap(히트맵) 형식으로 시각화**


TOT_LVPOP_CO컬럼 = 총 생활인구 수 (하루 누적)은
서울시에서 제공하는 시간대별 체류 인구를 24시간 누적한 수치로,
일반적으로 말하는 유동인구와 가장 유사한 개념입니다.

기존의 유동인구가 카드 사용, 교통량 등 간접적인 방식으로 추정된 데 비해,
생활인구는 이동통신사 기지국 접속 정보를 기반으로 실제 해당 지역에 머문 사람 수를 측정하기 때문에
더 정밀하고 신뢰할 수 있는 데이터입니다.

# 따라서, 이 데이터는 **유동인구의 현실적이고 정교한 버전**이라고 볼 수 있습니다.

In [ ]:
# 자치구별 위경도 중심 좌표
gu_coords = {
    "강남구": [37.5172, 127.0473], "강동구": [37.5301, 127.1238], "강북구": [37.6398, 127.0255],
    "강서구": [37.5509, 126.8495], "관악구": [37.4781, 126.9516], "광진구": [37.5384, 127.0823],
    "구로구": [37.4955, 126.8878], "금천구": [37.4569, 126.8958], "노원구": [37.6542, 127.0568],
    "도봉구": [37.6688, 127.0472], "동대문구": [37.5744, 127.0396], "동작구": [37.5124, 126.9392],
    "마포구": [37.5663, 126.9014], "서대문구": [37.5791, 126.9368], "서초구": [37.4836, 127.0326],
    "성동구": [37.5634, 127.0369], "성북구": [37.5894, 127.0167], "송파구": [37.5145, 127.1065],
    "양천구": [37.5169, 126.8664], "영등포구": [37.5264, 126.8963], "용산구": [37.5323, 126.9907],
    "은평구": [37.6027, 126.9291], "종로구": [37.5730, 126.9794], "중구": [37.5636, 126.9976],
    "중랑구": [37.5985, 127.0927]
}

# 좌표 & 인구수 기반 heat_data 생성
heat_data = []
for _, row in population_df.iterrows():
    gu = row['SIGNGU_NM']
    pop = float(row['TOT_LVPOP_CO'])
    coord = gu_coords.get(gu)
    if coord:
        # HeatMap 형식: [위도, 경도, 가중치]
        heat_data.append([coord[0], coord[1], pop])

# 지도 생성
seoul_map = folium.Map(location=[37.5665, 126.9780], zoom_start=11)

# HeatMap 레이어 추가
HeatMap(heat_data, radius=25, blur=20, max_zoom=13).add_to(seoul_map)

# 출력
seoul_map


# **서울시 자치구별 유동인구 대비 와이파이 설치 현황을 비교**

인구1만명당_와이파이수 값이 낮을수록 와이파이 설치가 필요한 지역이다.

In [ ]:
#유동인구 DataFrame 처리
population_df = pd.DataFrame(data['SPOP_DAILYSUM_JACHI']['row'])
pop_df = population_df[['SIGNGU_NM', 'TOT_LVPOP_CO']].copy()
pop_df.columns = ['자치구', '생활인구수']
pop_df['생활인구수'] = pop_df['생활인구수'].astype(float)
#와이파이 데이터 불러오기
wifi_df = pd.read_csv("서울시 공공와이파이 서비스 위치 정보.csv", encoding='cp949')

#와이파이 자치구별 개수 집계
wifi_filtered = wifi_df[(wifi_df['X좌표'].between(126, 129)) & (wifi_df['Y좌표'].between(33, 39))]
wifi_counts = wifi_filtered['자치구'].value_counts().reset_index()
wifi_counts.columns = ['자치구', '와이파이설치수']
wifi_counts['와이파이설치수'] = wifi_counts['와이파이설치수'].astype(int)


#데이터 병합 및 인구 대비 설치 비율 계산
merged = pd.merge(pop_df, wifi_counts, on='자치구', how='left').fillna(0)
merged['와이파이설치수'] = merged['와이파이설치수'].astype(int)
merged['인구1만명당_와이파이수'] = merged['와이파이설치수'] / (merged['생활인구수'] / 10000)
result = merged.sort_values(by='인구1만명당_와이파이수')

# 표 출력
pd.set_option('display.float_format', '{:,.2f}'.format)
result.rename(columns={
    '생활인구수': '하루 누적 총 생활인구 수'
}, inplace=True)

display(result)

자치구  하루 누적 총 생활인구 수  와이파이설치수  인구1만명당_와이파이수
0    서울시   10,628,652.79        0          0.00
23   강남구      797,954.64     1001         12.54
24   송파구      755,964.85     1111         14.70
8    성북구      431,809.89      713         16.51
21   관악구      479,264.34      794         16.57
22   서초구      544,734.68      935         17.16
19  영등포구      492,840.11      904         18.34
13  서대문구      372,321.30      739         19.85
20   동작구      392,040.61      859         21.91
25   강동구      511,908.07     1146         22.39
1    종로구      300,667.72      689         22.92
14   마포구      491,710.53     1141         23.20
7    중랑구      348,242.80      822         23.60
6   동대문구      367,652.38      874         23.77
5    광진구      401,969.79      961         23.91
11   노원구      485,861.09     1239         25.50
9    강북구      282,188.49      723         25.62
12   은평구      435,035.82     1127         25.91
3    용산구      302,802.46      816         26.95
17   구로구      408,590.07     1228         30.05
15   양천구      374,062.85     1183         31.63
16   강서구      542,485.77     1794         33.07
4    성동구      345,720.66     1191         34.45
18   금천구      211,912.66      757         35.72
10   도봉구      264,370.17      974         36.84
2     중구      286,541.02     1513         52.80

강남구는 인구 1만명당 사용하는 공용 와이파이가  약 12.54개로 서울의 자치구중 가장 낮다.
이를통해 강남구가 하루 누적 총 생활인구수에 비해 와이파이 설치수가 가장 부족한것을 할 수 있다.

***따라서 분석 및 개선 방안의 타겟을 강남구로 지정***






# **현재 설치되어있는 공용와이파이 현황을 시각화.**

**파란원의 범위가 평균적인 범위이다.(반경 200m)**

와이파이(Wi-Fi)의 최대 커버리지 거리는 약 200m 정도이며, 실내 환경에서는 40m 이내로 줄어들 수 있습니다. 실외에서는 개방된 공간에서 약 200m, 실내에서는 벽이나 장애물로 인해 신호가 약해지므로 40m 이내를 정상적인 서비스 범위로 볼 수 있습니다.

In [ ]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster

# 1. CSV 로드
df = pd.read_csv("서울시 공공와이파이 서비스 위치 정보.csv", encoding='cp949')

# 2. 강남구 + 유효 좌표 필터링
wifi_df = df[(df['자치구'] == '강동구') &
             (df['X좌표'].between(126.76, 127.20)) &
             (df['Y좌표'].between(37.40, 37.70))]

# 3. 중복 제거
wifi_df = wifi_df.drop_duplicates(subset=['X좌표', 'Y좌표'])

# 4. 지도 초기화
m = folium.Map(location=[37.4979, 127.0276], zoom_start=13)
marker_cluster = MarkerCluster().add_to(m)

# 5. 마커 + 반경 원 표시
for _, row in wifi_df.iterrows():
    lat, lon = row['Y좌표'], row['X좌표']

    # 마커
    folium.Marker(
        location=[lat, lon],
        popup=f"{row['와이파이명']}<br>{row['도로명주소']} {row['상세주소']}",
        icon=folium.Icon(color='blue')
    ).add_to(marker_cluster)

    # 실외 기준 커버리지 원 (반경 200m)
    folium.Circle(
        location=[lat, lon],
        radius=200,  # 미터 단위
        color='skyblue',
        fill=True,
        fill_opacity=0.2
    ).add_to(m)

# 6. 지도 출력
m

[자치구 외각라인 GeoJSON (GitHub)](https://github.com/cubensys/Korea_District/blob/master/3_%EC%84%9C%EC%9A%B8%EC%8B%9C_%EC%9E%90%EC%B9%98%EA%B5%AC/%EC%84%9C%EC%9A%B8_%EC%9E%90%EC%B9%98%EA%B5%AC_%EA%B2%BD%EA%B3%84_2017.geojson) 다운로드 및 파싱하여 자치구 선언시 해당 구역내에서만 파란원이 없는 부분에 빨간원(반경 200m)이 격자로 생긴다.
예)  area = "강남구" --> 빨간원은 강남구 범위 안에서만 생성.

파란원의 실제 커버리지값(buffer)의 바깥부분이면 빨간원 생성. 파란원의 커버리지 안쪽 범위와 빨간원의 중심점이 생성될 위치가 겹치면 생성 안됨.

In [ ]:
# 1. 자치구 외각라인 GeoJSON 다운로드 및 파싱
geojson_url = "https://raw.githubusercontent.com/cubensys/Korea_District/master/3_%EC%84%9C%EC%9A%B8%EC%8B%9C_%EC%9E%90%EC%B9%98%EA%B5%AC/%EC%84%9C%EC%9A%B8_%EC%9E%90%EC%B9%98%EA%B5%AC_%EA%B2%BD%EA%B3%84_2017.geojson"
response = requests.get(geojson_url)
geoJSON = response.json()

# 2. 설정값
area = "강남구"
gap = 400       # 빨간원 중심끼리의 간격 (m)
buffer = 200    # 파란 원 커버리지 반경 (m)
r = 200         # 빨간 원 반경 (m)

# 예) 버퍼값이 150이면 파란 원(Wi-Fi 커버)의 중심으로부터 반지름 150m까지 커버한다는 의미
# 즉, 커버 반경이 150m인 파란 원끼리 사이가 멀면 그 사이 빈 공간(50m 이상)에 빨간 원이 생길 수 있음
# 파란 원 커버(150m) 안에 격자 중심이 완전히 들어가면 빨간 원은 생기지 않음
# 반대로, 커버 경계 근처나 그 바깥의 격자점은 커버되지 않아 빨간 원이 생성됨


#파란원의 실제 커버반경의 끝부분에 빨간원의 중심이 생기는게 아닌 외각라인이 닿을수있게 생성되도록


# 3. 대상 자치구 polygon 추출
polygon = None
for feature in geoJSON['features']:
    if feature['properties'].get('SIG_KOR_NM') == area:
        polygon = shape(feature['geometry'])
        break
if polygon is None:
    raise ValueError(f"{area}에 해당하는 폴리곤을 찾을 수 없습니다.")

# 4. 좌표계 변환기 준비
transformer_to_5179 = Transformer.from_crs("EPSG:4326", "EPSG:5179", always_xy=True)
transformer_to_4326 = Transformer.from_crs("EPSG:5179", "EPSG:4326", always_xy=True)

# 5. polygon 좌표계 변환 및 경계 추출
polygon_proj = transform(transformer_to_5179.transform, polygon)
minx, miny, maxx, maxy = polygon_proj.bounds
if any(np.isnan([minx, miny, maxx, maxy])) or (maxx <= minx or maxy <= miny):
    raise ValueError("Polygon bounds가 비정상입니다.")

# 6. CSV 업로드 (Colab에서 uploaded = files.upload() 사용 시)
csv_filename = list(uploaded.keys())[0]
df = pd.read_csv(csv_filename, encoding='cp949')
wifi_df = df[(df['자치구'] == area) &
             (df['X좌표'].between(126.76, 127.20)) &
             (df['Y좌표'].between(37.40, 37.70))].drop_duplicates(subset=['X좌표', 'Y좌표'])

# 7. GeoDataFrame 생성 및 좌표 변환
geometry = [Point(xy) for xy in zip(wifi_df['X좌표'], wifi_df['Y좌표'])]
wifi_gdf = gpd.GeoDataFrame(wifi_df, geometry=geometry, crs='EPSG:4326')
wifi_gdf_meter = wifi_gdf.to_crs(epsg=5179)

# 8. 파란 원 커버리지 병합
cleaned_buffers = [geom.buffer(buffer).buffer(0) for geom in wifi_gdf_meter.geometry]
buffer_union = unary_union(cleaned_buffers)

# 9. 격자 포인트 생성
x_vals = np.arange(minx, maxx, gap)
y_vals = np.arange(miny, maxy, gap)

gap_points = []
for x in x_vals:
    for y in y_vals:
        pt = Point(x, y)
        if polygon_proj.contains(pt) and not buffer_union.contains(pt):
            gap_points.append(pt)

# 10. 빨간 원 중심 포인트들을 다시 WGS84로 변환
gap_points_wgs84 = [transform(transformer_to_4326.transform, pt) for pt in gap_points]
gap_gdf = gpd.GeoDataFrame(geometry=gap_points_wgs84, crs='EPSG:4326')

# 11. folium 지도 시각화
m = folium.Map(location=[37.4979, 127.0276], zoom_start=13)
marker_cluster = MarkerCluster().add_to(m)

# 12. 기존 와이파이 위치 + 파란 원 시각화
for _, row in wifi_df.iterrows():
    lat, lon = row['Y좌표'], row['X좌표']
    folium.Marker(
        location=[lat, lon],
        popup=f"{row['와이파이명']}<br>{row['도로명주소']} {row['상세주소']}",
        icon=folium.Icon(color='blue')
    ).add_to(marker_cluster)

    folium.Circle(
        location=[lat, lon],
        radius=200,
        color='skyblue',
        fill=True,
        fill_opacity=0.2
    ).add_to(m)

# 13. 추가 설치 지점(빨간 원) 표시
for _, row in gap_gdf.iterrows():
    lat, lon = row.geometry.y, row.geometry.x

    folium.CircleMarker(
        location=[lat, lon],
        radius=1,
        color='red',
        fill=True,
        fill_opacity=0.8
    ).add_to(m)

    folium.Circle(
        location=[lat, lon],
        radius=r,
        color='red',
        fill=True,
        fill_opacity=0.2
    ).add_to(m)

# 14. 지도 출력
m


# **빨간 원 생성 기준 조절 가능**

빨간원 생성 간격을 지정 가능하고,
파란원의 실제 커버리지 값을 조정해 빨간원이 더 세밀하게 생성되는지도 조절 가능.
예)  


gap = 400 -> 350        빨간원 중심끼리의 간격 (m)

buffer = 150 -> 100     파란 원 커버리지 반경 (m)

위의 값을 적용해 좀더 세밀하게 와이파이 설치 권장 위치를 표시하여 보다 원활한 와이파이 시설 이용을 가능하게 할 수 있다.





In [ ]:
# 1. 자치구 외각라인 GeoJSON 다운로드 및 파싱
geojson_url = "https://raw.githubusercontent.com/cubensys/Korea_District/master/3_%EC%84%9C%EC%9A%B8%EC%8B%9C_%EC%9E%90%EC%B9%98%EA%B5%AC/%EC%84%9C%EC%9A%B8_%EC%9E%90%EC%B9%98%EA%B5%AC_%EA%B2%BD%EA%B3%84_2017.geojson"
response = requests.get(geojson_url)
geoJSON = response.json()

# 2. 설정값
area = "강남구"
gap = 350       # 빨간원 중심끼리의 간격 (m)
buffer = 100    # 파란 원 커버리지 반경 (m)
r = 200         # 빨간 원 반경 (m)

# 예) 버퍼값이 150이면 파란 원(Wi-Fi 커버)의 중심으로부터 반지름 150m까지 커버한다는 의미
# 즉, 커버 반경이 150m인 파란 원끼리 사이가 멀면 그 사이 빈 공간(50m 이상)에 빨간 원이 생길 수 있음
# 파란 원 커버(150m) 안에 격자 중심이 완전히 들어가면 빨간 원은 생기지 않음
# 반대로, 커버 경계 근처나 그 바깥의 격자점은 커버되지 않아 빨간 원이 생성됨


#파란원의 실제 커버반경의 끝부분에 빨간원의 중심이 생기는게 아닌 외각라인이 닿을수있게 생성되도록


# 3. 대상 자치구 polygon 추출
polygon = None
for feature in geoJSON['features']:
    if feature['properties'].get('SIG_KOR_NM') == area:
        polygon = shape(feature['geometry'])
        break
if polygon is None:
    raise ValueError(f"{area}에 해당하는 폴리곤을 찾을 수 없습니다.")

# 4. 좌표계 변환기 준비
transformer_to_5179 = Transformer.from_crs("EPSG:4326", "EPSG:5179", always_xy=True)
transformer_to_4326 = Transformer.from_crs("EPSG:5179", "EPSG:4326", always_xy=True)

# 5. polygon 좌표계 변환 및 경계 추출
polygon_proj = transform(transformer_to_5179.transform, polygon)
minx, miny, maxx, maxy = polygon_proj.bounds
if any(np.isnan([minx, miny, maxx, maxy])) or (maxx <= minx or maxy <= miny):
    raise ValueError("Polygon bounds가 비정상입니다.")

# 6. CSV 업로드 (Colab에서 uploaded = files.upload() 사용 시)
csv_filename = list(uploaded.keys())[0]
df = pd.read_csv(csv_filename, encoding='cp949')
wifi_df = df[(df['자치구'] == area) &
             (df['X좌표'].between(126.76, 127.20)) &
             (df['Y좌표'].between(37.40, 37.70))].drop_duplicates(subset=['X좌표', 'Y좌표'])

# 7. GeoDataFrame 생성 및 좌표 변환
geometry = [Point(xy) for xy in zip(wifi_df['X좌표'], wifi_df['Y좌표'])]
wifi_gdf = gpd.GeoDataFrame(wifi_df, geometry=geometry, crs='EPSG:4326')
wifi_gdf_meter = wifi_gdf.to_crs(epsg=5179)

# 8. 파란 원 커버리지 병합
cleaned_buffers = [geom.buffer(buffer).buffer(0) for geom in wifi_gdf_meter.geometry]
buffer_union = unary_union(cleaned_buffers)

# 9. 격자 포인트 생성
x_vals = np.arange(minx, maxx, gap)
y_vals = np.arange(miny, maxy, gap)

gap_points = []
for x in x_vals:
    for y in y_vals:
        pt = Point(x, y)
        if polygon_proj.contains(pt) and not buffer_union.contains(pt):
            gap_points.append(pt)

# 10. 빨간 원 중심 포인트들을 다시 WGS84로 변환
gap_points_wgs84 = [transform(transformer_to_4326.transform, pt) for pt in gap_points]
gap_gdf = gpd.GeoDataFrame(geometry=gap_points_wgs84, crs='EPSG:4326')

# 11. folium 지도 시각화
m = folium.Map(location=[37.4979, 127.0276], zoom_start=13)
marker_cluster = MarkerCluster().add_to(m)

# 12. 기존 와이파이 위치 + 파란 원 시각화
for _, row in wifi_df.iterrows():
    lat, lon = row['Y좌표'], row['X좌표']
    folium.Marker(
        location=[lat, lon],
        popup=f"{row['와이파이명']}<br>{row['도로명주소']} {row['상세주소']}",
        icon=folium.Icon(color='blue')
    ).add_to(marker_cluster)

    folium.Circle(
        location=[lat, lon],
        radius=200,
        color='skyblue',
        fill=True,
        fill_opacity=0.2
    ).add_to(m)

# 13. 추가 설치 지점(빨간 원) 표시
for _, row in gap_gdf.iterrows():
    lat, lon = row.geometry.y, row.geometry.x

    folium.CircleMarker(
        location=[lat, lon],
        radius=1,
        color='red',
        fill=True,
        fill_opacity=0.8
    ).add_to(m)

    folium.Circle(
        location=[lat, lon],
        radius=r,
        color='red',
        fill=True,
        fill_opacity=0.2
    ).add_to(m)

# 14. 지도 출력
m


# **결론**
분석 결과,

예: 강남구는 생활인구(유동인구)에 비해 공용 와이파이 설치 수가 매우 부족하며

커버리지 분석을 통해, 기존 와이파이 반경 바깥에 미커버 지역(빨간 원)이 다수 발견됨
→ 따라서 강남구 및 유사한 자치구에는 공공 와이파이의 추가 설치가 시급하다.

# **기여**
통신 기반 생활인구 데이터 활용으로 정확도 향상

단순 개수 비교가 아닌 커버리지 모델링 + 격자 분석을 통한 입체적 접근 및 실제 커버리지를 분석해 사각지대까지 도출

행정적 단위와 공간 단위를 동시에 분석함으로써 정책/현장 모두에 실용적 인사이트 제공 -> 예산과 자원을 효율적으로 활용해 와이파이 설치의 실질적 효과 극대화

데이터 기반 정책: 생활인구 기준으로 설치 우선순위를 과학적으로 제시